## 산업부문 요인분해분석 예시코드

**참고사항**
* 광업, 제조업을 19개 업종으로 나누어 에너지, 온실가스 요인분해분석을 수행 
* 한국에너지공단 에너지, 온실가스 통계자료와 한국은행 국민계정(실질산출액, 실질부가가치액)을 활용 
* 해당코드는 python 3.7에서 작성되었습니다.

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline

In [2]:
# 데이터 불러오기
df = pd.read_excel('total_input.xlsx')
df.head()

실적년도  감축업종코드 감축업종코드명    실질산출액(백만원)  실질부가가치액(백만원)   석탄류(천toe)   석유류(천toe)  \
0  2011       1      광업  3.796199e+06  2.365625e+06   35.379990   21.930911   
1  2011       2    음식료품  9.892679e+07  1.721800e+07   31.338552  356.569321   
2  2011       3      섬유  8.421345e+07  1.786797e+07   79.273859  195.799004   
3  2011       4     목재   7.154951e+06  2.010102e+06  244.525355   21.946030   
4  2011       5      제지  3.334314e+07  1.062102e+07   52.852203  473.885984   

    가스류(천toe)  기타연료(천toe)     열(천toe)     전력(천toe)     합계(천toe)  석탄류(천tCO2)  \
0    0.078128    0.000000    0.107800    96.804241   154.301071  139.436559   
1  707.434415    9.210000  157.935973   833.840325  2096.328586  117.007696   
2  343.080913   11.827000  348.709005  1217.604782  2196.294563  295.517393   
3  160.746631    0.000000   11.580103   119.796444   558.594563  896.607615   
4  381.283795  287.297308  307.554734   896.013941  2398.887966  197.000381   

    석유류(천tCO2)  가스류(천tCO2)  기타연료(천tCO2)     열(천tCO2)   전력(천tCO2)    합계(천tCO2)  
0    70.335699     0.16825     0.000000     0.395267   509.81108   720.146855  
1   987.798086  1510.08146    33.770000   579.098567  4391.34344  7619.099249  
2   576.126473   725.45317    43.365667  1278.599685  6412.40925  9331.471639  
3    65.590916   340.52884     0.000000    42.460377   630.89797  1976.085718  
4  1590.116088   806.18153  1053.423463  1127.700692  4718.77984  9493.201994

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 171 entries, 0 to 170
Data columns (total 19 columns):
실적년도            171 non-null int64
감축업종코드          171 non-null int64
감축업종코드명         171 non-null object
실질산출액(백만원)      171 non-null float64
실질부가가치액(백만원)    171 non-null float64
석탄류(천toe)       171 non-null float64
석유류(천toe)       171 non-null float64
가스류(천toe)       171 non-null float64
기타연료(천toe)      171 non-null float64
열(천toe)         171 non-null float64
전력(천toe)        171 non-null float64
합계(천toe)        171 non-null float64
석탄류(천tCO2)      171 non-null float64
석유류(천tCO2)      171 non-null float64
가스류(천tCO2)      171 non-null float64
기타연료(천tCO2)     171 non-null float64
열(천tCO2)        171 non-null float64
전력(천tCO2)       171 non-null float64
합계(천tCO2)       171 non-null float64
dtypes: float64(16), int64(2), object(1)
memory usage: 25.5+ KB


### 에너지소비량 요인분해

**[참고] 요인분해분석결과 단계별 컬럼정리**

* 에너지 : Q    Si    Ii    QSiIi
* CO2    : Qi    Si    Ii    Mij    Cij


* 에너지 : Eit-Ei0    lnEit-lnEi0    ln(Qt/Q0)    ln(Sit/Si0)    ln(Iit/Ii0)
* CO2    : Cijt-Cij0    lnCijt-lnCij0    ln(Qt/Q0)    ln(Sit/Si0)    ln(Iit/Ii0)    ln(Mijt-Mij0)
            
            
* 에너지 : 생산효과, 구조효과, 원단위개선효과                   (Eact Estr Eins)
* CO2    : 생산효과, 구조효과, 에너지원단위효과, 에너지믹스효과 (Cact    Cstr Cint Cmix)
            
            
* 에너지 : 소비량증감 Etot
* CO2    : 배출량 증감 Ctot

**분석용 데이터 사전처리**

In [4]:
energy_df = df[['실적년도','감축업종코드','감축업종코드명','실질산출액(백만원)','실질부가가치액(백만원)','합계(천toe)',
               '석탄류(천toe)','석유류(천toe)','가스류(천toe)','기타연료(천toe)','열(천toe)','전력(천toe)']]
energy_df.columns =['year','code','name','out_value','add_value','energy','coal','petro','gas','others','heat','elec']
energy_df.head(3)

year  code  name     out_value     add_value       energy       coal  \
0  2011     1    광업  3.796199e+06  2.365625e+06   154.301071  35.379990   
1  2011     2  음식료품  9.892679e+07  1.721800e+07  2096.328586  31.338552   
2  2011     3    섬유  8.421345e+07  1.786797e+07  2196.294563  79.273859   

        petro         gas  others        heat         elec  
0   21.930911    0.078128   0.000    0.107800    96.804241  
1  356.569321  707.434415   9.210  157.935973   833.840325  
2  195.799004  343.080913  11.827  348.709005  1217.604782

** **
**산업부문 전체 에너지 요인분해분석(실질산출액 기준)**

In [7]:
def LMDI_out_energy(data, base_y, target_y):
    
    base  = data[data['year']== base_y].copy()      # 기준년도 데이터
    target  = data[data['year']== target_y].copy()  # 비교(실제)년도 데이터
    
    base['energy_b'] = base['energy']
    base['Q_b'] = sum(base['out_value'])/1000
    base['Si_b'] = (base['out_value']/1000)/ base['Q_b'] 
    base['li_b'] = base['energy']/(base['out_value']/1000)
    #base['QSili_b'] = base['Q_b']*base['Si_b']*base['li_b']
    base = base.drop(['coal','petro','gas','others','heat','elec','energy'], axis=1)
    
    target['energy_t'] = target['energy']
    target['Q_t'] = sum(target['out_value'])/1000
    target['Si_t'] = (target['out_value']/1000)/target['Q_t']
    target['li_t'] = target['energy']/(target['out_value']/1000)
    #target['QSili_t'] = target['Q_t']*target['Si_t']*target['li_t']
    target = target.drop(['name','out_value','add_value','coal','petro','gas','others','heat','elec','energy'], axis=1)
    
    result_df_temp = pd.merge(base, target, on='code')
    
    result_df = pd.DataFrame()
    result_df['Eit-Ei0'] = result_df_temp['energy_t']-result_df_temp['energy_b']
    result_df['lnEit-lnEi0'] = np.log(result_df_temp['energy_t'])-np.log(result_df_temp['energy_b'])
    result_df['ln(Qt/Q0)'] = np.log(result_df_temp['Q_t']/result_df_temp['Q_b'])
    result_df['ln(Sit/Si0)'] = np.log(result_df_temp['Si_t']/result_df_temp['Si_b'])
    result_df['ln(Iit/Ii0)'] = np.log(result_df_temp['li_t']/result_df_temp['li_b'])
    
    result_df['Eact'] = (result_df['Eit-Ei0']/result_df['lnEit-lnEi0'])*result_df['ln(Qt/Q0)']   # 생산효과
    result_df['Estr'] = (result_df['Eit-Ei0']/result_df['lnEit-lnEi0'])*result_df['ln(Sit/Si0)'] # 기준효과
    result_df['Eins'] = (result_df['Eit-Ei0']/result_df['lnEit-lnEi0'])*result_df['ln(Iit/Ii0)'] # 원단위개선효과
    result_df['Etot'] = result_df['Eact'] + result_df['Estr'] + result_df['Eins']                # 소비량증감

    print('< 산업전체 에너지 요인분해분석(실질산출액 기준),',base_y,'vs',target_y,'>\n')
    print('생산효과:',       np.round(sum(result_df['Eact']), 2))
    print('구조효과:',       np.round(sum(result_df['Estr']), 2))
    print('원단위효과:', np.round(sum(result_df['Eins']), 2))
    print('소비량증감:',     np.round(sum(result_df['Etot']), 2))

In [8]:
LMDI_out_energy(energy_df, 2015, 2018)

< 산업전체 에너지 요인분해분석(실질산출액 기준), 2015 vs 2018 >

생산효과: 7773.65
구조효과: 4095.65
원단위효과: 277.36
소비량증감: 12146.66


** **
**산업부문 전체 에너지 요인분해분석(실질부가가치액 기준)**

In [13]:
def LMDI_add_energy(data, base_y, target_y):
    
    base  = data[data['year']== base_y].copy()      # 기준년도 데이터
    target  = data[data['year']== target_y].copy()  # 비교(실제)년도 데이터
    
    base['energy_b'] = base['energy']
    base['Q_b'] = sum(base['add_value'])/1000
    base['Si_b'] = (base['add_value']/1000)/ base['Q_b'] 
    base['li_b'] = base['energy']/(base['add_value']/1000)
    #base['QSili_b'] = base['Q_b']*base['Si_b']*base['li_b']
    base = base.drop(['coal','petro','gas','others','heat','elec','energy'], axis=1)
    
    target['energy_t'] = target['energy']
    target['Q_t'] = sum(target['add_value'])/1000
    target['Si_t'] = (target['add_value']/1000)/target['Q_t']
    target['li_t'] = target['energy']/(target['add_value']/1000)
    #target['QSili_t'] = target['Q_t']*target['Si_t']*target['li_t']
    target = target.drop(['name','add_value','add_value','coal','petro','gas','others','heat','elec','energy'], axis=1)
    
    result_df_temp = pd.merge(base, target, on='code')
    
    result_df = pd.DataFrame()
    result_df['Eit-Ei0'] = result_df_temp['energy_t']-result_df_temp['energy_b']
    result_df['lnEit-lnEi0'] = np.log(result_df_temp['energy_t'])-np.log(result_df_temp['energy_b'])
    result_df['ln(Qt/Q0)'] = np.log(result_df_temp['Q_t']/result_df_temp['Q_b'])
    result_df['ln(Sit/Si0)'] = np.log(result_df_temp['Si_t']/result_df_temp['Si_b'])
    result_df['ln(Iit/Ii0)'] = np.log(result_df_temp['li_t']/result_df_temp['li_b'])
    
    result_df['Eact'] = (result_df['Eit-Ei0']/result_df['lnEit-lnEi0'])*result_df['ln(Qt/Q0)']   # 생산효과
    result_df['Estr'] = (result_df['Eit-Ei0']/result_df['lnEit-lnEi0'])*result_df['ln(Sit/Si0)'] # 구조효과
    result_df['Eins'] = (result_df['Eit-Ei0']/result_df['lnEit-lnEi0'])*result_df['ln(Iit/Ii0)'] # 원단위개선효과
    result_df['Etot'] = result_df['Eact'] + result_df['Estr'] + result_df['Eins']                # 소비량증감

    print('< 산업전체 에너지 요인분해분석(실질부가가치액 기준),',base_y,'vs',target_y,'>\n')
    print('기준년도:', base_y, 'vs', '비교년도:', target_y) 
    print('생산효과:',       np.round(sum(result_df['Eact']), 2))
    print('구조효과:',       np.round(sum(result_df['Estr']), 2))
    print('원단위효과:', np.round(sum(result_df['Eins']), 2))
    print('소비량증감:',     np.round(sum(result_df['Etot']), 2))

In [14]:
LMDI_add_energy(energy_df, 2015, 2018)

< 산업전체 에너지 요인분해분석(실질부가가치액 기준), 2015 vs 2018 >

기준년도: 2015 vs 비교년도: 2018
생산효과: 11088.42
구조효과: -5325.43
원단위효과: 6383.67
소비량증감: 12146.66


** **
**산업부문 업종별 에너지 요인분해분석(실질산출액 기준)**

In [23]:
def LMDI_sector_out_energy(data, base_y, target_y):
    
    base  = data[data['year']== base_y].copy()      # 기준년도 데이터
    target  = data[data['year']== target_y].copy()  # 비교(실제)년도 데이터
    
    base['energy_b'] = base['energy']
    base['Q_b'] = base['out_value']/1000
    base['li_b'] = base['energy']/(base['out_value']/1000)
    base = base.drop(['coal','petro','gas','others','heat','elec','energy'], axis=1)
    
    target['energy_t'] = target['energy']
    target['Q_t'] = target['out_value']/1000
    target['li_t'] = target['energy']/(target['out_value']/1000)
    target = target.drop(['name','out_value','add_value','coal','petro','gas','others','heat','elec','energy'], axis=1)
    
    result_df_temp = pd.merge(base, target, on='code')
    
    result_df = pd.DataFrame()
    result_df['Eit-Ei0'] = result_df_temp['energy_t']-result_df_temp['energy_b']
    result_df['lnEit-lnEi0'] = np.log(result_df_temp['energy_t'])-np.log(result_df_temp['energy_b'])
    result_df['ln(Qt/Q0)'] = np.log(result_df_temp['Q_t']/result_df_temp['Q_b'])
    result_df['ln(Iit/Ii0)'] = np.log(result_df_temp['li_t']/result_df_temp['li_b'])
    
    result_df_last = pd.DataFrame()
    result_df_last['업종명'] = result_df_temp['name']
    result_df_last['생산효과'] = (result_df['Eit-Ei0']/result_df['lnEit-lnEi0'])*result_df['ln(Qt/Q0)']     # 생산효과
    result_df_last['원단위효과'] = (result_df['Eit-Ei0']/result_df['lnEit-lnEi0'])*result_df['ln(Iit/Ii0)'] # 원단위효과
    result_df_last['소비량증감'] = result_df_last['생산효과'] + result_df_last['원단위효과']                # 소비량증감

    print('< 업종별 에너지 요인분해분석(실질산출액 기준),',base_y,'vs',target_y,'>\n')
    return result_df_last

In [24]:
LMDI_sector_out_energy(energy_df, 2015, 2018)

< 업종별 에너지 요인분해분석(실질산출액 기준), 2015 vs 2018 >



업종명         생산효과        원단위효과        소비량증감
0      광업    -4.528632     8.629997     4.101365
1    음식료품   144.889982   284.782299   429.672281
2      섬유  -218.321876   172.420122   -45.901754
3     목재     26.952878  -102.123254   -75.170376
4      제지    32.672597   162.276369   194.948965
5      정유  5345.462260 -1265.844106  4079.618155
6    석유화학  2795.996919   526.064636  3322.061555
7      유리    30.401605   -28.727519     1.674085
8      요업    72.741891    -7.574957    65.166934
9     시멘트   682.625961 -1002.910000  -320.284039
10     철강  1552.493192   444.785088  1997.278280
11   비철금속    64.496919   169.968379   234.465298
12    기계    383.340807   390.038483   773.379290
13   반도체   1370.557377  -535.584167   834.973210
14  디스플레이     4.167798    53.524521    57.692319
15   전기전자   -91.284353   484.197200   392.912847
16    자동차  -110.275799   328.261365   217.985565
17     조선  -273.960812   192.007847   -81.952965
18   기타제조    60.869248     3.172065    64.041313

** **
**산업부문 업종별 에너지 요인분해분석(실질부가가치액 기준)**

In [21]:
def LMDI_sector_add_energy(data, base_y, target_y):
    
    base  = data[data['year']== base_y].copy()      # 기준년도 데이터
    target  = data[data['year']== target_y].copy()  # 비교(실제)년도 데이터
    
    base['energy_b'] = base['energy']
    base['Q_b'] = base['add_value']/1000
    base['li_b'] = base['energy']/(base['add_value']/1000)
    base = base.drop(['coal','petro','gas','others','heat','elec','energy'], axis=1)
    
    target['energy_t'] = target['energy']
    target['Q_t'] = target['add_value']/1000
    target['li_t'] = target['energy']/(target['add_value']/1000)
    target = target.drop(['name','out_value','add_value','coal','petro','gas','others','heat','elec','energy'], axis=1)
    
    index_df_temp = pd.merge(base, target, on='code')
    
    index_df = pd.DataFrame()
    index_df['Eit-Ei0'] = index_df_temp['energy_t']-index_df_temp['energy_b']
    index_df['lnEit-lnEi0'] = np.log(index_df_temp['energy_t'])-np.log(index_df_temp['energy_b'])
    index_df['ln(Qt/Q0)'] = np.log(index_df_temp['Q_t']/index_df_temp['Q_b'])
    index_df['ln(Iit/Ii0)'] = np.log(index_df_temp['li_t']/index_df_temp['li_b'])
    
    result_df = pd.DataFrame()
    result_df['업종명'] = index_df_temp['name']
    result_df['생산효과'] = (index_df['Eit-Ei0']/index_df['lnEit-lnEi0'])*index_df['ln(Qt/Q0)']     # 생산효과
    result_df['원단위효과'] = (index_df['Eit-Ei0']/index_df['lnEit-lnEi0'])*index_df['ln(Iit/Ii0)'] # 원단위개선효과
    result_df['소비량증감'] = result_df['생산효과'] + result_df['원단위효과']                       # 소비량증감

    print('< 업종별 에너지 요인분해분석(실질부가가치액 기준),',base_y,'vs',target_y,'>\n')
    return result_df

In [22]:
LMDI_sector_add_energy(energy_df, 2015, 2018)

< 업종별 에너지 요인분해분석(실질부가가치액 기준), 2015 vs 2018 >



업종명         생산효과        원단위효과        소비량증감
0      광업    -6.055879    10.157244     4.101365
1    음식료품   159.089228   270.583053   429.672281
2      섬유  -343.585710   297.683956   -45.901754
3     목재     21.356790   -96.527167   -75.170376
4      제지   122.501247    72.447718   194.948965
5      정유   809.354810  3270.263345  4079.618155
6    석유화학  2110.197783  1211.863772  3322.061555
7      유리    62.689808   -61.015723     1.674085
8      요업    86.629813   -21.462878    65.166934
9     시멘트   836.387996 -1156.672035  -320.284039
10     철강   740.035842  1257.242439  1997.278280
11   비철금속  -153.825671   388.290969   234.465298
12    기계    322.407497   450.971793   773.379290
13   반도체   1403.658308  -568.685098   834.973210
14  디스플레이   -87.389756   145.082075    57.692319
15   전기전자   -93.779580   486.692428   392.912847
16    자동차  -134.950565   352.936131   217.985565
17     조선  -126.695350    44.742385   -81.952965
18   기타제조    34.965906    29.075407    64.041313

### 이산화탄소배출량 요인분해

**분석용 데이터 작업**

In [27]:
energy_df = df[['실적년도','감축업종코드','감축업종코드명','실질산출액(백만원)','실질부가가치액(백만원)','합계(천toe)',
               '석탄류(천toe)','석유류(천toe)','가스류(천toe)','기타연료(천toe)','열(천toe)','전력(천toe)']]
energy_df.columns =['year','code','name','out_value','add_value','t_energy','coal','petro','gas','others','heat','elec']
energy_df_2 = energy_df.drop('t_energy', axis=1)
energy_df_2 = pd.melt(energy_df_2, id_vars=['year','code','name','out_value','add_value'])
energy_df_2 = energy_df_2.sort_values(['year','code'])
energy_df_2.columns =['year','code','name','out_value','add_value','energy_name','energy']
energy_df_2.head()

year  code name  out_value  add_value energy_name     energy
0    2011     1   광업  3796199.0  2365625.0        coal  35.379990
171  2011     1   광업  3796199.0  2365625.0       petro  21.930911
342  2011     1   광업  3796199.0  2365625.0         gas   0.078128
513  2011     1   광업  3796199.0  2365625.0      others   0.000000
684  2011     1   광업  3796199.0  2365625.0        heat   0.107800

In [28]:
CO2_df_sub = df[['실적년도','감축업종코드','합계(천tCO2)','석탄류(천tCO2)','석유류(천tCO2)','가스류(천tCO2)','기타연료(천tCO2)','열(천tCO2)','전력(천tCO2)']]
CO2_df_sub.columns =['year','code','t_CO2','coal','petro','gas','others','heat','elec']
CO2_df_sub_2 = CO2_df_sub.drop('t_CO2', axis=1)
CO2_df_sub_2 = pd.melt(CO2_df_sub_2, id_vars=['year','code'])
CO2_df_sub_2 = CO2_df_sub_2.sort_values(['year','code'])
CO2_df_sub_2.columns =['year','code','energy_name','CO2']
CO2_df_sub_2.head(10)

year  code energy_name          CO2
0    2011     1        coal   139.436559
171  2011     1       petro    70.335699
342  2011     1         gas     0.168250
513  2011     1      others     0.000000
684  2011     1        heat     0.395267
855  2011     1        elec   509.811080
1    2011     2        coal   117.007696
172  2011     2       petro   987.798086
343  2011     2         gas  1510.081460
514  2011     2      others    33.770000

In [29]:
CO2_df = pd.merge(energy_df_2, CO2_df_sub_2, on=['year','code','energy_name']) # 업종별 에너지사용량, 온실가스배출량
CO2_df.head()

year  code name  out_value  add_value energy_name     energy         CO2
0  2011     1   광업  3796199.0  2365625.0        coal  35.379990  139.436559
1  2011     1   광업  3796199.0  2365625.0       petro  21.930911   70.335699
2  2011     1   광업  3796199.0  2365625.0         gas   0.078128    0.168250
3  2011     1   광업  3796199.0  2365625.0      others   0.000000    0.000000
4  2011     1   광업  3796199.0  2365625.0        heat   0.107800    0.395267

In [30]:
energy_df_s = energy_df[['year','code','t_energy']] # 업종별 총 에너지사용량 출력 
CO2_df_sub_s = CO2_df_sub[['year','code','t_CO2']]  # 업종별 총 CO2배출량 출력

In [31]:
CO2_df = pd.merge(CO2_df, energy_df_s, on=['year','code'])
CO2_df = pd.merge(CO2_df, CO2_df_sub_s, on=['year','code'])
CO2_df.head()

year  code name  out_value  add_value energy_name     energy         CO2  \
0  2011     1   광업  3796199.0  2365625.0        coal  35.379990  139.436559   
1  2011     1   광업  3796199.0  2365625.0       petro  21.930911   70.335699   
2  2011     1   광업  3796199.0  2365625.0         gas   0.078128    0.168250   
3  2011     1   광업  3796199.0  2365625.0      others   0.000000    0.000000   
4  2011     1   광업  3796199.0  2365625.0        heat   0.107800    0.395267   

     t_energy       t_CO2  
0  154.301071  720.146855  
1  154.301071  720.146855  
2  154.301071  720.146855  
3  154.301071  720.146855  
4  154.301071  720.146855

** **
**산업부문 전체 이산화탄소 요인분해분석(실질산출액 기준)**

In [34]:
def LMDI_out_CO2(data, base_y, target_y):
    
    base  = data[data['year']== base_y].copy()      # 기준년도 데이터
    target  = data[data['year']== target_y].copy()  # 비교(실제)년도 데이터
    
    base['CO2_b'] = base['CO2']
    base['Qi_b'] = (sum(base['out_value'])/6)/1000
    base['Si_b'] = (base['out_value']/1000)/ base['Qi_b'] 
    base['li_b'] = base['t_energy']/(base['out_value']/1000)
    base['Mij_b'] = base['CO2']/base['t_energy']
    base['Cij_b'] = base['Qi_b']*base['Si_b']*base['li_b']*base['Mij_b']
    
    target['CO2_t'] =target['CO2']
    target['Qi_t'] = (sum(target['out_value'])/6)/1000
    target['Si_t'] = (target['out_value']/1000)/ target['Qi_t'] 
    target['li_t'] = target['t_energy']/(target['out_value']/1000)
    target['Mij_t'] = target['CO2']/target['t_energy']
    target['Cij_t'] = target['Qi_t']*target['Si_t']*target['li_t']*target['Mij_t']

    result_df_temp = pd.merge(base, target, on=['code', 'energy_name'])
    
    result_df = pd.DataFrame()
    result_df['Cijt-Cij0'] = result_df_temp['CO2_t']-result_df_temp['CO2_b']
    result_df['lnCijt-lnCij0'] = np.log(result_df_temp['CO2_t'])-np.log(result_df_temp['CO2_b'])
    result_df['ln(Qt/Q0)'] = np.log(result_df_temp['Qi_t']/result_df_temp['Qi_b'])
    result_df['ln(Sit/Si0)'] = np.log(result_df_temp['Si_t']/result_df_temp['Si_b'])
    result_df['ln(Iit/Ii0)'] = np.log(result_df_temp['li_t']/result_df_temp['li_b'])
    result_df['ln(Mijt-Mij0)'] = np.log(result_df_temp['Mij_t']/result_df_temp['Mij_b'])
    
    result_df['Cact'] = (result_df['Cijt-Cij0']/result_df['lnCijt-lnCij0'])*result_df['ln(Qt/Q0)']     # 생산효과
    result_df['Cstr'] = (result_df['Cijt-Cij0']/result_df['lnCijt-lnCij0'])*result_df['ln(Sit/Si0)']   # 구조효과
    result_df['Cint'] = (result_df['Cijt-Cij0']/result_df['lnCijt-lnCij0'])*result_df['ln(Iit/Ii0)']   # 원단위개선효과
    result_df['Cmix'] = (result_df['Cijt-Cij0']/result_df['lnCijt-lnCij0'])*result_df['ln(Mijt-Mij0)'] # 에너지믹스효과
    result_df['Ctot'] = result_df['Cact'] + result_df['Cstr'] + result_df['Cint'] + result_df['Cmix']   # 배출량증감

    result_df = result_df.fillna(0)
   #return result_df

    
    print('< 산업전체 CO2 요인분해분석(실질산출액 기준),',base_y,'vs',target_y,'>\n')
    print('생산효과:',         np.round(sum(result_df['Cact']), 2))
    print('구조효과:',         np.round(sum(result_df['Cstr']), 2))
    print('원단위효과:',       np.round(sum(result_df['Cint']), 2))
    print('에너지믹스효과:',   np.round(sum(result_df['Cmix']), 2))
    print('배출량증감:',       np.round(sum(result_df['Ctot']), 2))

In [35]:
LMDI_out_CO2(CO2_df, 2015, 2018)

< 산업전체 CO2 요인분해분석(실질산출액 기준), 2015 vs 2018 >

생산효과: 20258.11
구조효과: 6034.36
원단위효과: 3938.94
에너지믹스효과: -368.19
배출량증감: 29863.22


C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:24: RuntimeWarning: divide by zero encountered in log
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:28: RuntimeWarning: divide by zero encountered in log


** **
**산업부문 전체 이산화탄소 요인분해분석(실질부가가치액 기준)**

In [38]:
def LMDI_add_CO2(data, base_y, target_y):
    
    base  = data[data['year']== base_y].copy()      # 기준년도 데이터
    target  = data[data['year']== target_y].copy()  # 비교(실제)년도 데이터
    
    base['CO2_b'] = base['CO2']
    base['Qi_b'] = (sum(base['add_value'])/6)/1000
    base['Si_b'] = (base['add_value']/1000)/ base['Qi_b'] 
    base['li_b'] = base['t_energy']/(base['add_value']/1000)
    base['Mij_b'] = base['CO2']/base['t_energy']
    base['Cij_b'] = base['Qi_b']*base['Si_b']*base['li_b']*base['Mij_b']
    
    target['CO2_t'] =target['CO2']
    target['Qi_t'] = (sum(target['add_value'])/6)/1000
    target['Si_t'] = (target['add_value']/1000)/ target['Qi_t'] 
    target['li_t'] = target['t_energy']/(target['add_value']/1000)
    target['Mij_t'] = target['CO2']/target['t_energy']
    target['Cij_t'] = target['Qi_t']*target['Si_t']*target['li_t']*target['Mij_t']

    result_df_temp = pd.merge(base, target, on=['code', 'energy_name'])
    
    result_df = pd.DataFrame()
    result_df['Cijt-Cij0'] = result_df_temp['CO2_t']-result_df_temp['CO2_b']
    result_df['lnCijt-lnCij0'] = np.log(result_df_temp['CO2_t'])-np.log(result_df_temp['CO2_b'])
    result_df['ln(Qt/Q0)'] = np.log(result_df_temp['Qi_t']/result_df_temp['Qi_b'])
    result_df['ln(Sit/Si0)'] = np.log(result_df_temp['Si_t']/result_df_temp['Si_b'])
    result_df['ln(Iit/Ii0)'] = np.log(result_df_temp['li_t']/result_df_temp['li_b'])
    result_df['ln(Mijt-Mij0)'] = np.log(result_df_temp['Mij_t']/result_df_temp['Mij_b'])
    
    result_df['Cact'] = (result_df['Cijt-Cij0']/result_df['lnCijt-lnCij0'])*result_df['ln(Qt/Q0)']     # 생산효과
    result_df['Cstr'] = (result_df['Cijt-Cij0']/result_df['lnCijt-lnCij0'])*result_df['ln(Sit/Si0)']   # 구조효과
    result_df['Cint'] = (result_df['Cijt-Cij0']/result_df['lnCijt-lnCij0'])*result_df['ln(Iit/Ii0)']   # 원단위개선효과
    result_df['Cmix'] = (result_df['Cijt-Cij0']/result_df['lnCijt-lnCij0'])*result_df['ln(Mijt-Mij0)'] # 에너지믹스효과
    result_df['Ctot'] = result_df['Cact'] + result_df['Cstr'] + result_df['Cint'] + result_df['Cmix']   # 배출량증감

    result_df = result_df.fillna(0)
   #return result_df

    
    print('< 산업전체 CO2 요인분해분석(실질부가가치액 기준),',base_y,'vs',target_y,'>\n')
    print('생산효과:',         np.round(sum(result_df['Cact']), 2))
    print('구조효과:',         np.round(sum(result_df['Cstr']), 2))
    print('원단위효과:',       np.round(sum(result_df['Cint']), 2))
    print('에너지믹스효과:',   np.round(sum(result_df['Cmix']), 2))
    print('배출량증감:',       np.round(sum(result_df['Ctot']), 2))

In [39]:
LMDI_add_CO2(CO2_df, 2015, 2018)

< 산업전체 CO2 요인분해분석(실질부가가치액 기준), 2015 vs 2018 >

생산효과: 28896.4
구조효과: -12154.17
원단위효과: 13489.17
에너지믹스효과: -368.19
배출량증감: 29863.22


C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:24: RuntimeWarning: divide by zero encountered in log
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:28: RuntimeWarning: divide by zero encountered in log


** **
**산업부문 업종별 이산화탄소 요인분해분석(실질산출액 기준)**

In [40]:
CO2_df.head()

year  code name  out_value  add_value energy_name     energy         CO2  \
0  2011     1   광업  3796199.0  2365625.0        coal  35.379990  139.436559   
1  2011     1   광업  3796199.0  2365625.0       petro  21.930911   70.335699   
2  2011     1   광업  3796199.0  2365625.0         gas   0.078128    0.168250   
3  2011     1   광업  3796199.0  2365625.0      others   0.000000    0.000000   
4  2011     1   광업  3796199.0  2365625.0        heat   0.107800    0.395267   

     t_energy       t_CO2  
0  154.301071  720.146855  
1  154.301071  720.146855  
2  154.301071  720.146855  
3  154.301071  720.146855  
4  154.301071  720.146855

In [64]:
def LMDI_sector_out_CO2(data, base_y, target_y):
    
    base  = data[data['year']== base_y].copy()      # 기준년도 데이터
    target  = data[data['year']== target_y].copy()  # 비교(실제)년도 데이터
    
    base['CO2_b'] = base['CO2']
    base['Qi_b'] = base['out_value']/1000
    base['li_b'] = base['t_energy']/(base['out_value']/1000)
    base['Mij_b'] = base['CO2']/base['t_energy']
    base['Cij_b'] = base['Qi_b']*base['li_b']*base['Mij_b']
    
    target['CO2_t'] =target['CO2']
    target['Qi_t'] = target['out_value']/1000
    target['li_t'] = target['t_energy']/(target['out_value']/1000)
    target['Mij_t'] = target['CO2']/target['t_energy']
    target['Cij_t'] = target['Qi_t']*target['li_t']*target['Mij_t']

    result_df_temp = pd.merge(base, target, on=['code', 'name','energy_name'])
    
    result_df = pd.DataFrame()
    result_df['code'] = result_df_temp['code']
    result_df['Cijt-Cij0'] = result_df_temp['CO2_t']-result_df_temp['CO2_b']
    result_df['lnCijt-lnCij0'] = np.log(result_df_temp['CO2_t'])-np.log(result_df_temp['CO2_b'])
    result_df['ln(Qt/Q0)'] = np.log(result_df_temp['Qi_t']/result_df_temp['Qi_b'])
    result_df['ln(Iit/Ii0)'] = np.log(result_df_temp['li_t']/result_df_temp['li_b'])
    result_df['ln(Mijt-Mij0)'] = np.log(result_df_temp['Mij_t']/result_df_temp['Mij_b'])
    
    result_df['Cact'] = (result_df['Cijt-Cij0']/result_df['lnCijt-lnCij0'])*result_df['ln(Qt/Q0)']     # 생산효과
    result_df['Cint'] = (result_df['Cijt-Cij0']/result_df['lnCijt-lnCij0'])*result_df['ln(Iit/Ii0)']   # 원단위개선효과
    result_df['Cmix'] = (result_df['Cijt-Cij0']/result_df['lnCijt-lnCij0'])*result_df['ln(Mijt-Mij0)'] # 에너지믹스효과
    result_df['Ctot'] = result_df['Cact'] + result_df['Cint'] + result_df['Cmix']   # 배출량증감

    result_df = result_df.fillna(0)
    
    index_df = result_df_temp[['code', 'name']].drop_duplicates()      # 업종명 열 생성
    result_df_sub = result_df[['code','Cact','Cint','Cmix','Ctot']]    # 분석효과 열만 추출
    result_df_sub = result_df_sub.groupby(['code']).sum()
    result_df_last = pd.merge(index_df, result_df_sub, on='code')
    result_df_last = result_df_last.drop(['code'], axis=1)
    result_df_last.columns = ['업종명','생산효과','원단위효과','에너지믹스효과','배출량증감']
    return result_df_last

In [67]:
LMDI_sector_out_CO2(CO2_df, 2015, 2018)

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:23: RuntimeWarning: divide by zero encountered in log
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:26: RuntimeWarning: divide by zero encountered in log


업종명         생산효과        원단위효과      에너지믹스효과        배출량증감
0      광업   -20.997003    40.012980     3.691018    22.706996
1    음식료품   547.010169  1075.152412   282.113517  1904.276098
2      섬유  -867.821456   685.363665  -374.396736  -556.854528
3     목재    105.361608  -399.210442   -73.989764  -367.838598
4      제지   127.737867   634.441072  -575.611672   186.567267
5      정유  5631.134442 -1333.493343 -2850.874141  1446.766957
6    석유화학  4960.721630   933.355899  1850.410253  7744.487783
7      유리   111.406906  -105.272207    28.490458    34.625156
8      요업   245.477135   -25.562694   -92.571261   127.343180
9     시멘트  2617.985306 -3846.328435    35.659497 -1192.683631
10     철강  6032.435067  1728.276282  2088.391575  9849.102924
11   비철금속   261.505645   689.144399  -235.118098   715.531946
12    기계   1738.001707  1768.367824   389.855124  3896.224654
13   반도체   6569.474132 -2567.208341  -190.456419  3811.809371
14  디스플레이    20.455642   262.699506  -136.217424   146.937724
15   전기전자  -417.722623  2215.715151  -126.648448  1671.344080
16    자동차  -441.454048  1314.089845  -380.996845   491.638952
17     조선 -1218.867170   854.253786   -74.217840  -438.831224
18   기타제조   290.621156    15.145074    64.294566   370.060796

** **
**산업부문 업종별 이산화탄소 요인분해분석(실질부가가치액 기준)**

In [68]:
def LMDI_sector_add_CO2(data, base_y, target_y):
    
    base  = data[data['year']== base_y].copy()      # 기준년도 데이터
    target  = data[data['year']== target_y].copy()  # 비교(실제)년도 데이터
    
    base['CO2_b'] = base['CO2']
    base['Qi_b'] = base['add_value']/1000
    base['li_b'] = base['t_energy']/(base['add_value']/1000)
    base['Mij_b'] = base['CO2']/base['t_energy']
    base['Cij_b'] = base['Qi_b']*base['li_b']*base['Mij_b']
    
    target['CO2_t'] =target['CO2']
    target['Qi_t'] = target['add_value']/1000
    target['li_t'] = target['t_energy']/(target['add_value']/1000)
    target['Mij_t'] = target['CO2']/target['t_energy']
    target['Cij_t'] = target['Qi_t']*target['li_t']*target['Mij_t']

    result_df_temp = pd.merge(base, target, on=['code', 'name','energy_name'])
    
    result_df = pd.DataFrame()
    result_df['code'] = result_df_temp['code']
    result_df['Cijt-Cij0'] = result_df_temp['CO2_t']-result_df_temp['CO2_b']
    result_df['lnCijt-lnCij0'] = np.log(result_df_temp['CO2_t'])-np.log(result_df_temp['CO2_b'])
    result_df['ln(Qt/Q0)'] = np.log(result_df_temp['Qi_t']/result_df_temp['Qi_b'])
    result_df['ln(Iit/Ii0)'] = np.log(result_df_temp['li_t']/result_df_temp['li_b'])
    result_df['ln(Mijt-Mij0)'] = np.log(result_df_temp['Mij_t']/result_df_temp['Mij_b'])
    
    result_df['Cact'] = (result_df['Cijt-Cij0']/result_df['lnCijt-lnCij0'])*result_df['ln(Qt/Q0)']     # 생산효과
    result_df['Cint'] = (result_df['Cijt-Cij0']/result_df['lnCijt-lnCij0'])*result_df['ln(Iit/Ii0)']   # 원단위개선효과
    result_df['Cmix'] = (result_df['Cijt-Cij0']/result_df['lnCijt-lnCij0'])*result_df['ln(Mijt-Mij0)'] # 에너지믹스효과
    result_df['Ctot'] = result_df['Cact'] + result_df['Cint'] + result_df['Cmix']   # 배출량증감

    result_df = result_df.fillna(0)
    
    index_df = result_df_temp[['code', 'name']].drop_duplicates()      # 업종명 열 생성
    result_df_sub = result_df[['code','Cact','Cint','Cmix','Ctot']]    # 분석효과 열만 추출
    result_df_sub = result_df_sub.groupby(['code']).sum()
    result_df_last = pd.merge(index_df, result_df_sub, on='code')
    result_df_last = result_df_last.drop(['code'], axis=1)
    result_df_last.columns = ['업종명','생산효과','원단위효과','에너지믹스효과','배출량증감']
    return result_df_last

In [69]:
LMDI_sector_add_CO2(CO2_df, 2015, 2018)

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:23: RuntimeWarning: divide by zero encountered in log
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:26: RuntimeWarning: divide by zero encountered in log


업종명         생산효과        원단위효과      에너지믹스효과        배출량증감
0      광업   -28.078085    47.094063     3.691018    22.706996
1    음식료품   600.617270  1021.545310   282.113517  1904.276098
2      섬유 -1365.740606  1183.282815  -374.396736  -556.854528
3     목재     83.485920  -377.334754   -73.989764  -367.838598
4      제지   478.934939   283.244000  -575.611672   186.567267
5      정유   852.608348  3445.032751 -2850.874141  1446.766957
6    석유화학  3743.961130  2150.116399  1850.410253  7744.487783
7      유리   229.727265  -223.592567    28.490458    34.625156
8      요업   292.343763   -72.429322   -92.571261   127.343180
9     시멘트  3207.688559 -4436.031688    35.659497 -1192.683631
10     철강  2875.515451  4885.195898  2088.391575  9849.102924
11   비철금속  -623.693068  1574.343112  -235.118098   715.531946
12    기계   1461.740494  2044.629037   389.855124  3896.224654
13   반도체   6728.136374 -2725.870583  -190.456419  3811.809371
14  디스플레이  -428.910816   712.065963  -136.217424   146.937724
15   전기전자  -429.140931  2227.133459  -126.648448  1671.344080
16    자동차  -540.231615  1412.867412  -380.996845   491.638952
17     조선  -563.674787   199.061403   -74.217840  -438.831224
18   기타제조   166.945253   138.820977    64.294566   370.060796